In [1]:
import random
import csv
import urllib.parse
import re
from SPARQLWrapper import JSON, SPARQLWrapper
from collections import defaultdict
import pandas as pd

WIKIDATA_ENDPOINT = "https://query.wikidata.org/sparql"
sparql = SPARQLWrapper("https://query.wikidata.org/sparql", agent="Mozilla/5.0 (X11; Linux x86_64) AppleWebKit/537.11 (KHTML, like Gecko) Chrome/23.0.1271.64 Safari/537.11")


prefix = """
	PREFIX wd: <http://www.wikidata.org/entity/>
    PREFIX wds: <http://www.wikidata.org/entity/statement/>
    PREFIX wdv: <http://www.wikidata.org/value/>
    PREFIX wdt: <http://www.wikidata.org/prop/direct/>
    PREFIX wikibase: <http://wikiba.se/ontology#>
    PREFIX p: <http://www.wikidata.org/prop/>
    PREFIX ps: <http://www.wikidata.org/prop/statement/>
    PREFIX pq: <http://www.wikidata.org/prop/qualifier/>
    PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
    PREFIX bd: <http://www.bigdata.com/rdf#>
    PREFIX xsd: <http://www.w3.org/2001/XMLSchema#>
"""

test_num = 100

def write_csv(fname, data):
	with open(fname, 'w') as f:
		write = csv.writer(f)
		write.writerows(data)

def query_sparql(query):
	sparql.setQuery(prefix+query)
	sparql.setReturnFormat(JSON)

	results = sparql.query().convert()

	return results



def print_examples(training_data, test):
	num = 2
	print("training_data_example")
	for x in range(num):
		print(training_data[x])

	print()
	print("test_data_example")
	for x in range(num):
		print(test[x])

def getPronouns(gender, val_type="subj"):
	if gender == "female":
		if val_type == "subj":
			return "she"
		elif val_type == "poss" or val_type == "obj":
			return "her"
	elif gender == "male":
		if val_type == "subj":
			return "he"
		elif val_type == "poss":
			return "his"
		elif val_type == "obj":
			return "him"
	else:
		if val_type == "subj":
			return "they"
		elif val_type == "poss":
			return "their"
		elif val_type == "obj":
			return "them"
	return "they"

In [2]:
import logging
#import logging_helper
from collections import defaultdict
from SPARQLWrapper import SPARQLWrapper, JSON
#PREFIXES = constants.PREFIXES
PREFIXES = prefix
WIKIDATA_ENDPOINT = "https://query.wikidata.org/sparql"
sparql = SPARQLWrapper("https://query.wikidata.org/sparql", agent="Mozilla/5.0 (X11; Linux x86_64) AppleWebKit/537.11 (KHTML, like Gecko) Chrome/23.0.1271.64 Safari/537.11")


def clean_wikidata_id(wikidata_link):
    return wikidata_link.replace('http://www.wikidata.org/entity/', '')

class WikidataHelper():
    def __init__(self, logger=None, wikidata_host=WIKIDATA_ENDPOINT):
        self.sparql = SPARQLWrapper(wikidata_host)

    def get_wikidata_id_by_label(self, entity_label, instance_of_id=None):
        retval = None

        if not entity_label:
            return retval

        instance_of_query = """
        BIND(wd:%s AS ?idType)
        {?s wdt:P31 ?idType. }
            UNION
            {?s wdt:P31 ?idNode .
            ?idNode wdt:P279 ?idType.}
                UNION
            {?s wdt:P31 ?idNode1 .
            ?idNode1 wdt:P279 ?idNode2.
            ?idNode2 wdt:P279 ?idType.}
        """ % instance_of_id if instance_of_id else ""

        query = """
        %s

        SELECT ?s (COUNT(?oedge) as ?count)
        WHERE
        {


            ?s rdfs:label '%s'@en .
            ?s wdt:P31 ?instance_of.
            FILTER (?instance_of not in ( wd:Q4167410 )  ) # filter disambiguation page
            %s
            ?s ?oedge ?other .

        } GROUP BY ?s ORDER BY DESC(?count)
        """ % (PREFIXES, entity_label, instance_of_query)
        self.sparql.setQuery(query)
        self.sparql.setReturnFormat(JSON)
        try:
            results = self.sparql.query().convert()
            retval = clean_wikidata_id(results['results']['bindings'][0]['s']['value'])
        except Exception as e:
            print("error")#self.logger.info("[get_wikidata_id_by_label] Exception: {}\nquery={}".format(e, query))
        return retval


    def get_instance_of(self, wikidata_id):
        """

        :param wikidata_id:
        :return:
        """
        retval = []
        if not wikidata_id:
            return retval
        query = """
        %s
        SELECT DISTINCT ?oLabel
        WHERE
        {   wd:%s wdt:P31 ?o .
            ?o rdfs:label ?oLabel
            FILTER ( lang(?oLabel) = "en" )


        }
        """ % (PREFIXES, wikidata_id)
        self.sparql.setQuery(query)
        self.sparql.setReturnFormat(JSON)
        try:
            results = self.sparql.query().convert()
            retval = [x['oLabel']['value'] for x in results['results']['bindings']]
        except Exception as e:
            print("error")#self.logger.info("[get_instance_of] Exception: {}\nquery={}".format(e, query))
        return retval

    def get_entity_all_outgoing_relations(self, wikidata_id):
        """
        all info includes all statements and identifiers in Wikidata page. Exclude alias, description
        :param wikidata_id:
        :return:
        """
        retval = {}

        if not wikidata_id:
            return retval

        query = """
        %s
        SELECT DISTINCT ?sLabel ?rel ?relName ?o ?oLabel
        WHERE
        {   wd:%s rdfs:label ?sLabel .
            wd:%s ?directClaimP ?o .          # Get the truthy triples.
            ?rel wikibase:directClaim ?directClaimP . # Find the Wikibase properties linked
                             # to the truthy triples' predicates

         FILTER (lang(?sLabel) = 'en')

         OPTIONAL {
           ?rel rdfs:label ?relName .
            FILTER ( lang(?relName) = "en" )  }
         OPTIONAL {
            ?o rdfs:label ?oLabel
            FILTER ( lang(?oLabel) = "en" )
           }

        }
        """% (PREFIXES, wikidata_id, wikidata_id)
        self.sparql.setQuery(query)
        self.sparql.setReturnFormat(JSON)
        try:
            results = self.sparql.query().convert()
            entity_lable = results['results']['bindings'][0]['sLabel']['value']
            retval['label'] = entity_lable
            relations = {}

            for r in results['results']['bindings']:
                relation_id = clean_wikidata_id(r['rel']['value'])
                object_id = clean_wikidata_id(r['o']['value']) if 'oLabel' in r else None
                object_label = r['oLabel']['value'] if 'oLabel' in r else r['o']['value']
                if relation_id in relations:
                    relations[relation_id]['values'].append({'object_id': object_id, 'object_label': object_label})
                else:
                    relations[relation_id] = {}
                    relations[relation_id]['relation_label'] = r['relName']['value']
                    relations[relation_id]['values'] = [{'object_id': object_id, 'object_label': object_label}]

            retval['relations'] = relations
        except Exception as e:
            print("error")#self.logger.info("[get_entity_all_info] Exception: {}\nquery={}".format(e, query))
        return retval

    def get_entity_all_incoming_relations(self, wikidata_id):
        """
        get all direct incoming relations
        :param wikidata_id:
        :return:
        """
        retval = {}

        if not wikidata_id:
            return retval

        query = """
        %s
        SELECT DISTINCT  ?s ?sLabel ?rel ?relName ?oLabel
        WHERE
        {   wd:%s rdfs:label ?oLabel .

            ?s ?directClaimP wd:%s .          # Get the truthy triples.
            ?rel wikibase:directClaim ?directClaimP . # Find the Wikibase properties linked to the truthy triples' predicates


         FILTER (lang(?oLabel) = 'en')

         OPTIONAL {
           ?rel rdfs:label ?relName .
            FILTER ( lang(?relName) = "en" )  }
         OPTIONAL {
            ?s rdfs:label ?sLabel
            FILTER ( lang(?sLabel) = "en" )
           }
        }
        """ % (PREFIXES, wikidata_id, wikidata_id)
        self.sparql.setQuery(query)
        self.sparql.setReturnFormat(JSON)
        try:
            results = self.sparql.query().convert()
            entity_lable = results['results']['bindings'][0]['oLabel']['value']
            retval['label'] = entity_lable
            relations = {}

            for r in results['results']['bindings']:
                relation_id = clean_wikidata_id(r['rel']['value'])
                subject_id = clean_wikidata_id(r['s']['value']) if 'sLabel' in r else None
                subject_label = r['sLabel']['value'] if 'sLabel' in r else r['s']['value']
                if relation_id in relations:
                    relations[relation_id]['values'].append({'subject_id': subject_id, 'subject_label': subject_label})
                else:
                    relations[relation_id] = {}
                    relations[relation_id]['relation_label'] = r['relName']['value']
                    relations[relation_id]['values'] = [{'subject_id': subject_id, 'subject_label': subject_label}]

            retval['relations'] = relations
        except Exception as e:
            print("error")#self.logger.info("[get_entity_incoming_edges] Exception: {}\nquery={}".format(e, query))
        return retval


    def get_entity_relation(self, wikidata_id, relation_id, is_outgoing_relation=True):
        """
        Get specific incoming/outgoing relation info
        :param wikidata_id: wikidata id for the node
        :param relation_id: wikidata id for the specific relation
        :param is_outgoing_relation: True for outgoing relations, False for incoming ones.
        :return: list of linked nodes with the wikidata_id and title.
        """
        retval = []

        if not wikidata_id:
            return retval

        relation_query = "wd:{} wdt:{} ?otherNode".format(wikidata_id, relation_id) if is_outgoing_relation \
            else '?otherNode wdt:{} wd:{}'.format(relation_id, wikidata_id)

        query = """
        %s
        SELECT DISTINCT  ?otherNode ?otherNodeLabel
        WHERE
        {   wd:%s rdfs:label ?nodeLabel .

            %s

         FILTER (lang(?nodeLabel) = 'en')

         OPTIONAL {
            ?otherNode rdfs:label ?otherNodeLabel
            FILTER ( lang(?otherNodeLabel) = "en" )
           }
        }
        """ % (PREFIXES, wikidata_id, relation_query)
        self.sparql.setQuery(query)
        self.sparql.setReturnFormat(JSON)
        try:
            results = self.sparql.query().convert()

            for r in results['results']['bindings']:
                retval.append({
                    'label': clean_wikidata_id(r['otherNodeLabel']['value']),
                    'wikidata_id': clean_wikidata_id(r['otherNode']['value'])
                })
        except Exception as e:
            print("error")#self.logger.info("[get_entity_relation] Exception: {}\nquery={}".format(e, query))
        return retval


    def get_two_hop_path(self, source_node_id, target_node_id):
        """
        Find 2 hop path between source node and target node


        :param source_node_id:
        :param target_node_id:
        :return:
        """
        query = f"""
        {PREFIXES}
        SELECT DISTINCT  ?sourceNodeLabel ?relation1Label ?bridgeNode ?bridgeNodeLabel ?relation2Label ?targetNodeLabel
        WHERE
        {{   wd:{source_node_id} rdfs:label ?sourceNodeLabel .
            wd:{target_node_id} rdfs:label ?targetNodeLabel .
         FILTER (lang(?sourceNodeLabel) = 'en')
         FILTER (lang(?targetNodeLabel) = 'en')

         # relation: source -> relation1 -> bridge node -> relation2 -> target node
        {{ wd:{source_node_id} ?directClaimP ?bridgeNode .
            ?relations1 wikibase:directClaim ?directClaimP .
           ?bridgeNode ?otherDirectClaimP wd:{target_node_id} .
            ?relations2 wikibase:directClaim ?otherDirectClaimP .}}

         # relation: source -> relation1 -> bridge node <- relation2 <- target node
         UNION {{
            wd:{source_node_id} ?directClaimP ?bridgeNode .
           ?relations1 wikibase:directClaim ?directClaimP .
           wd:{target_node_id} ?otherDirectClaimP ?bridgeNode  .
           ?relations2 wikibase:directClaim ?otherDirectClaimP .
         }}

         # relation: source <- relations1 <- bridge node <- relations2 <- target node
        UNION {{
           ?bridgeNode ?directClaimP wd:{source_node_id}.
           ?relations1 wikibase:directClaim ?directClaimP .
           wd:{target_node_id} ?otherDirectClaimP ?bridgeNode  .
           ?relations2 wikibase:directClaim ?otherDirectClaimP .
         }}

         # relation: source <- relations1 <- bridge node -> relations2 -> target node
        UNION {{
         ?bridgeNode ?directClaimP wd:{source_node_id}.
           ?relations1 wikibase:directClaim ?directClaimP .
           ?bridgeNode ?otherDirectClaimP wd:{target_node_id}   .
           ?relations2 wikibase:directClaim ?otherDirectClaimP .
         }}


         OPTIONAL {{
            ?bridgeNode rdfs:label ?bridgeNodeLabel
            FILTER ( lang(?bridgeNodeLabel) = "en" )
           }}

         OPTIONAL {{
           ?relations1 rdfs:label ?relation1Label
                      FILTER ( lang(?relation1Label) = "en" )
         }}
         OPTIONAL {{
           ?relations2 rdfs:label ?relation2Label
                           FILTER ( lang(?relation2Label) = "en" )
         }}
        }}

        """
        retval = []
        self.sparql.setQuery(query)
        self.sparql.setReturnFormat(JSON)
        try:
            results = self.sparql.query().convert()

            for r in results['results']['bindings']:
                retval.append({
                    'sourceNodeLabel': r['sourceNodeLabel']['value'],
                    'relation1Label': r['relation1Label']['value'],
                    'bridgeNode': clean_wikidata_id(r['bridgeNode']['value']),
                    'bridgeNodeLabel': r['bridgeNodeLabel']['value'],
                    'relation2Label': r['relation2Label']['value'],
                    'targetNodeLabel': r['targetNodeLabel']['value']})

        except Exception as e:
            print("error")
            #self.logger.info("[get_two_hop_path] Exception: {}\nquery={}".format(e, query))
        return retval

In [3]:
pop_df = pd.read_csv("sports_popularity.csv")
pop_df['entity_type'].unique()
filter_list = ['cricket_team', 'rugby_team', 'american_football_team', 'canadian_football_club', 'baseball_team', 'ice_hockey_team', 'basketball_team', 'soccer_club']

# Filter the DataFrame based on the filter list
pop_df = pop_df[pop_df['entity_type'].isin(filter_list)]

In [4]:
helper = WikidataHelper()
helper.get_entity_all_incoming_relations('Q26876')

{'label': 'Taylor Swift',
 'relations': {'P175': {'relation_label': 'performer',
   'values': [{'subject_id': 'Q129982', 'subject_label': 'Crazier'},
    {'subject_id': 'Q21100', 'subject_label': 'Both of Us'},
    {'subject_id': 'Q154078', 'subject_label': 'Safe & Sound'},
    {'subject_id': 'Q18478957', 'subject_label': 'The 1989 World Tour'},
    {'subject_id': 'Q18333025', 'subject_label': 'Welcome to New York'},
    {'subject_id': 'Q18441355', 'subject_label': 'Blank Space'},
    {'subject_id': 'Q18786715', 'subject_label': 'Style'},
    {'subject_id': 'Q276585', 'subject_label': 'I Knew You Were Trouble'},
    {'subject_id': 'Q276589', 'subject_label': 'Back to December'},
    {'subject_id': 'Q104120195', 'subject_label': 'Dorothea'},
    {'subject_id': 'Q104120227', 'subject_label': 'Long Story Short'},
    {'subject_id': 'Q104120219', 'subject_label': 'Cowboy like Me'},
    {'subject_id': 'Q104148872', 'subject_label': 'No Body, No Crime'},
    {'subject_id': 'Q104120231', 'sub

In [4]:
# get popularity data
def top_n_pruning(lst, n, visited):
    count_dict = dict(zip(pop_df['wikidata_id'], pop_df['count']))
    for item in lst:
        object_id = item.get('object_id', None)
        subject_id = item.get('subject_id', None)
        if object_id is not None:
            count = count_dict.get(object_id, 0)
        elif subject_id is not None:
            count = count_dict.get(subject_id, 0)
        else:
            count = 0
        item['count'] = count
    sorted_list = sorted(lst, key=lambda x: x['count'], reverse=True)
    filtered_data = [item for item in sorted_list if ('object_id' not in item or item['object_id'] not in visited) and ('subject_id' not in item or item['subject_id'] not in visited)]
    if len(filtered_data) == 0:
        return None
    else:
        return filtered_data[:n]

def filter_sentences(sentences, mandatory):
    filtered_sentences = []
    for path_str, words in sentences:
        if all(word in path_str for word in mandatory):
            filtered_sentences.append((path_str, words))
    return filtered_sentences


from typing import List, Tuple
from datetime import datetime

def generate_n_hop_paths(helper, q_node: str, n_hops: int, cur_str: str = '', cur_hop: int = 0, visited: set = None,
                         mandatory_list: set = None, excluded_list: set = None, keep_list: set = None, branch: bool = False) -> List[Tuple[str, List[str]]]:
    if visited is None:
        visited = set()
    visited.add(q_node)


    if cur_hop == n_hops:
        return [(cur_str, [q_node])]

    if q_node not in SAVED_NODES_OUT:
        time.sleep(1)
        outgoing_relations = helper.get_entity_all_outgoing_relations(q_node)
        SAVED_NODES_OUT[q_node] = outgoing_relations
    else:
        outgoing_relations = SAVED_NODES_OUT[q_node]
    if q_node not in SAVED_NODES_IN:
        time.sleep(1)
        incoming_relations = helper.get_entity_all_incoming_relations(q_node)
        SAVED_NODES_IN[q_node] = incoming_relations
    else:
        incoming_relations = SAVED_NODES_IN[q_node]
    paths = []
    #keep_list = ['part of', 'performer', 'tracklist', 'record label', 'genre']
    # Process outgoing relations
    for r in outgoing_relations:
        if r == 'label' and cur_hop == 0:
            start_node = outgoing_relations[r]
            cur_str = start_node
        elif r != 'label':
            for rels in outgoing_relations[r]:
                relation_label = outgoing_relations[r][rels]['relation_label']
                if relation_label in keep_list:
                    if len(outgoing_relations[r][rels]['values']) > 10:
                        pruned_list = top_n_pruning(outgoing_relations[r][rels]['values'], 10, visited)
                    else:
                        pruned_list = outgoing_relations[r][rels]['values']
                    if pruned_list is None:  # Check if pruned_list is None
                        continue
                    for val in pruned_list:
                        if relation_label == "inception":
                            try:
                                dt = datetime.strptime(val["object_label"], '%Y-%m-%dT%H:%M:%SZ')
                                updated_str = cur_str + " --> " + relation_label + ' --> ' + dt.strftime("%Y")
                            except ValueError:
                                pass
                        else:
                            updated_str = cur_str + " --> " + relation_label + ' --> ' + val['object_label']
                        next_q_node = val['object_id']
                        new_visited = visited.copy()
                        new_visited.add(next_q_node)
                        sub_paths = generate_n_hop_paths(helper, next_q_node, n_hops,
                                                         updated_str, cur_hop + 1, new_visited,
                                                         mandatory_list, excluded_list, keep_list, branch)
                        for sub_path in sub_paths:
                            path_str, q_nodes = sub_path
                            paths.append((path_str, [q_node] + q_nodes))

    # Process incoming relations
    for r in incoming_relations:
        if r != 'label':
            for rels in incoming_relations[r]:
                relation_label = incoming_relations[r][rels]['relation_label']
                if relation_label in keep_list:
                    if len(incoming_relations[r][rels]['values']) > 10:
                        pruned_list = top_n_pruning(incoming_relations[r][rels]['values'], 10, visited)
                    else:
                        pruned_list = incoming_relations[r][rels]['values']
                    if pruned_list is None:  # Check if pruned_list is None
                        continue
                    for val in pruned_list:
                        updated_str = cur_str + " --> " + "~" + relation_label + ' --> ' + val['subject_label']
                        prev_q_node = val['subject_id']
                        new_visited = visited.copy()
                        new_visited.add(prev_q_node)
                        sub_paths = generate_n_hop_paths(helper, prev_q_node,
                                                         n_hops, updated_str, cur_hop + 1,
                                                         new_visited, mandatory_list,
                                                         excluded_list, keep_list, branch)
                        for sub_path in sub_paths:
                            path_str, q_nodes = sub_path
                            paths.append((path_str, [q_node] + q_nodes))
    paths = filter_sentences(paths, mandatory_list)
    if len(paths) > 10:
        paths = paths[:10]
    return paths

import random
def generate_trees(shape_inp, shape_num_hops, start_q_node, n_hops, mandatory_list, excluded_list, full_list, branch):
    helper = WikidataHelper()
    ori_path_list = generate_n_hop_paths(helper, start_q_node, n_hops,
                                         mandatory_list=mandatory_list,
                                         excluded_list=excluded_list,
                                         keep_list=full_list)
    #if len(shape_inp)==0:
    #    return ori_path_list
    aditional_path_list = []
    final_path = []
    for (path, nodes) in ori_path_list:
        skip = False
        temp_str = path
        temp_nodes = []
        for i, shape in enumerate(shape_inp):
            additions = generate_n_hop_paths(helper, nodes[shape], shape_num_hops[i],
                                             mandatory_list=mandatory_list,
                                             excluded_list=excluded_list,
                                             keep_list=full_list, branch=branch)
            addition_path = [t[0] for t in additions]   # [1, 2, 3]
            addition_q_node = [t[1] for t in additions]
            non_overlapping_nodes = []
            non_overlapping_paths = []
            for n, p in zip(addition_q_node, addition_path):
                if n[1] not in nodes and n[1] not in temp_nodes:
                    non_overlapping_nodes.append(n)
                    non_overlapping_paths.append(p)
            if len(non_overlapping_paths) != 0:
                index = random.randint(0, len(non_overlapping_paths)-1)
                temp_str+= ' | ' + non_overlapping_paths[index]
                temp_nodes.append(non_overlapping_nodes[index])
            else:
                skip = True
                break
        if skip == True:
            continue
        final_path.append(temp_str)
    return final_path

if __name__ == "__main__":

    helper = WikidataHelper()
    """
    n_hops = 2
    shape = [0]
    n_hops_shape = [1]

    """
    n_hops = 2
    shape = [0, 0]
    n_hops_shape = [1, 2]
    start_q_node = 'Q18786715'

    # path_list = generate_n_hop_paths(helper, start_q_node, n_hops)
    #path_list = generate_trees(shape, n_hops_shape, start_q_node, n_hops)
    #for p in path_list:
    #   print(p)
   # result = helper.get_two_hop_path(source_node_id='Q37175', target_node_id='Q295463')
   # for r in result:
   #    print(r)

In [5]:
import ast
import pandas as pd
df_sum = pd.read_csv("team_select.csv")

In [6]:
import json

# Open the JSON file
with open('team_path_constraints.txt', 'r') as file:
    # Load the JSON data
    slot_dict = json.load(file)

In [11]:
import pickle


In [8]:
SAVED_NODES_OUT


{'Q7156': {'label': 'FC Barcelona',
  'relations': {'P17': {'relation_label': 'country',
    'values': [{'object_id': 'Q29', 'object_label': 'Spain'}]},
   'P1532': {'relation_label': 'country for sport',
    'values': [{'object_id': 'Q29', 'object_label': 'Spain'}]},
   'P112': {'relation_label': 'founded by',
    'values': [{'object_id': 'Q115500',
      'object_label': 'Hans Max Gamper-Haessig'}]},
   'P276': {'relation_label': 'location',
    'values': [{'object_id': 'Q159848', 'object_label': 'Camp Nou'}]},
   'P115': {'relation_label': 'home venue',
    'values': [{'object_id': 'Q159848', 'object_label': 'Camp Nou'},
     {'object_id': 'Q1094423', 'object_label': 'Ciutat Esportiva Joan Gamper'},
     {'object_id': 'Q930832', 'object_label': 'Palau Blaugrana'}]},
   'P1830': {'relation_label': 'owner of',
    'values': [{'object_id': 'Q159848', 'object_label': 'Camp Nou'},
     {'object_id': 'Q1094423', 'object_label': 'Ciutat Esportiva Joan Gamper'},
     {'object_id': 'Q1030045'

In [13]:
import time
from datetime import datetime

def remove_prefix(strings):
    return [" --> ".join(string.split(' --> ')[2:]) for string in strings]

def replace(strings, rating):
    flag = False
    final_out = []
    name = strings[0].split(' | ')[0].split(' --> ')[0]
    for i, string in enumerate(strings):
        seperate_lst = string.split(' | ')
        modified = []
        for item in seperate_lst:
            if len(item.split(' --> '))==3 and flag == False:
                modified.append(name + " --> rating --> " + rating)
                flag = True
            else:
                modified.append(item)
        final_out.append(" | ".join(modified))
    return final_out


def add_rating(strings, rating):
    return [rating + " --> ~rating --> " + string for string in strings]
def add_specifiers(strings, specifiers):
    return [random.choice(specifiers) + " --> ~specifier --> " + string for string in strings]

def generate_paths_with_da_constraints(path_to_shapes, slot_dict, specifiers):
    with open("out_info.pkl", 'rb') as file:
        SAVED_NODES_OUT = pickle.load(file)

    with open("in_info.pkl", 'rb') as file:
        SAVED_NODES_IN = pickle.load(file)
    info = pd.read_csv(path_to_shapes)
    paths = []
    rating_df = pd.read_csv("team_select.csv")
    for da, value in slot_dict.items():
        mand = value['mandatory']
        excld = value['excluded']
        full = value['full']
        min_slots = value['min_slots']
        max_slots = value['max_slots']
        for index, row in info.iterrows():
            if row['not generate'] == 'X' or row['num_nodes'] < min_slots or row['num_nodes'] > max_slots:
                continue
            branch_loc = ast.literal_eval(row['branch_loc'])
            n_hops_shape = ast.literal_eval(row['n_hops_shape'])
            n_hops = row["Depth/Hops"]
            shape = row['Shape']
            for n, song in df_sum.iterrows():
                print("DA:{} shape:{} {}:60".format(da, shape, n))
                print(song['wiki_id'])
                if row['branch'] == "no":
                    branch = False
                else:
                    branch = True

                if da == "give_opinion" or da == "verify_attribute":
                    path_list = generate_trees(branch_loc, n_hops_shape, song['wiki_id'], n_hops-1, mand, excld, full, branch)
                else:
                    path_list = generate_trees(branch_loc, n_hops_shape, song['wiki_id'], n_hops, mand, excld, full, branch)
                count = 0
                while len(path_list) == 0 and count <=3:
                    if song['wiki_id'] in SAVED_NODES_OUT:
                        del SAVED_NODES_OUT[song['wiki_id']]
                    if song['wiki_id'] in SAVED_NODES_IN:
                        del SAVED_NODES_IN[song['wiki_id']]
                    if da == "give_opinion":
                        path_list = generate_trees(branch_loc, n_hops_shape, song['wiki_id'], n_hops-1, mand, excld, full, branch)
                    else:
                        path_list = generate_trees(branch_loc, n_hops_shape, song['wiki_id'], n_hops, mand, excld, full, branch)
                    count += 1
                if da == "request_explanation":
                    path_list = remove_prefix(path_list)
                    rating=rating_df.loc[n]['rating']
                    path_list = add_rating(path_list, rating)
                elif da == "request":
                    path_list = remove_prefix(path_list)
                    path_list = add_specifiers(path_list, specifiers)
                elif da == "give_opinion" or da == "verify_attribute":
                    rating=rating_df.loc[n]['rating']
                    path_list = add_rating(path_list, rating)
                elif da == "inform" and row['inform replace rating']=='yes' and random.random() < 1/10:
                    rating=rating_df.loc[n]['rating']
                    if len(path_list) == 0:
                        continue
                    path_list = replace(path_list, rating)

                for p in path_list:
                    path_data = {"da":da, "shape":shape, "path":p, "n_hops":n_hops}
                    paths.append(path_data)
                df = pd.DataFrame(paths)
                df.to_csv("musician_path_with_shapes.csv", index=False)
                print(len(SAVED_NODES_OUT))
                print(len(SAVED_NODES_IN))
            with open("out_info.pkl", 'wb') as json_file:
                pickle.dump(SAVED_NODES_OUT, json_file)

            with open("in_info.pkl", 'wb') as json_file_1:
                pickle.dump(SAVED_NODES_IN, json_file_1)

            with open("out_info.pkl", 'rb') as file:
                SAVED_NODES_OUT = pickle.load(file)

            with open("in_info.pkl", 'rb') as file:
                SAVED_NODES_IN = pickle.load(file)

specifiers = [
    # Positive
    "competitive",
    "disciplined",
    "experienced",
    "resilient",
    "versatile",

    # Negative
    "clumsy",
    "selfish",
    "uncoordinated",
    "undisciplined",
    "unmotivated",
]
path_to_shapes = "shapes.csv"
SAVED_NODES_OUT = {}
SAVED_NODES_IN = {}
generate_paths_with_da_constraints(path_to_shapes, slot_dict, specifiers)

DA:give_opinion shape:(X (X (X))) 0:60
Q18656
3563
3563
DA:give_opinion shape:(X (X (X))) 1:60
Q8682
3563
3563
DA:give_opinion shape:(X (X (X))) 2:60
Q1130849
3563
3563
DA:give_opinion shape:(X (X (X))) 3:60
Q9616
3563
3563
DA:give_opinion shape:(X (X (X))) 4:60
Q483020
3563
3563
DA:give_opinion shape:(X (X (X))) 5:60
Q7156
3563
3563
DA:give_opinion shape:(X (X (X))) 6:60
Q9617
3563
3563
DA:give_opinion shape:(X (X (X))) 7:60
Q50602
3563
3563
DA:give_opinion shape:(X (X (X))) 8:60
Q18741
3563
3563
DA:give_opinion shape:(X (X (X))) 9:60
Q157376
3563
3563
DA:give_opinion shape:(X (X (X))) 10:60
Q15789
3563
3563
DA:give_opinion shape:(X (X (X))) 11:60
Q18529
3563
3563
DA:give_opinion shape:(X (X (X))) 12:60
Q1422
3563
3563
DA:give_opinion shape:(X (X (X))) 13:60
Q19490
3563
3563
DA:give_opinion shape:(X (X (X))) 14:60
Q1543
3563
3563
DA:give_opinion shape:(X (X (X))) 15:60
Q18716
3563
3563
DA:give_opinion shape:(X (X (X))) 16:60
Q121783
3563
3563
DA:give_opinion shape:(X (X (X))) 17:60
Q2

error
error
error
error
error
3563
3563
DA:give_opinion shape:(X (X (X) (X))) 15:60
Q18716
error
error
error
3563
3563
DA:give_opinion shape:(X (X (X) (X))) 16:60
Q121783
error
error
error
error
error
error
error
3563
3563
DA:give_opinion shape:(X (X (X) (X))) 17:60
Q2739
error
error
error
error
error
3563
3563
DA:give_opinion shape:(X (X (X) (X))) 18:60
Q631
error
error
error
error
3563
3563
DA:give_opinion shape:(X (X (X) (X))) 19:60
Q81888
error
error
error
error
error
3563
3563
DA:give_opinion shape:(X (X (X) (X))) 20:60
Q131371
error
error
error
error
3563
3563
DA:give_opinion shape:(X (X (X) (X))) 21:60
Q41420
error
error
error
error
error
error
error
error
3563
3563
DA:give_opinion shape:(X (X (X) (X))) 22:60
Q5794
error
3563
3563
DA:give_opinion shape:(X (X (X) (X))) 23:60
Q18711
3563
3563
DA:give_opinion shape:(X (X (X) (X))) 24:60
Q1128631
error
error
error
3563
3563
DA:give_opinion shape:(X (X (X) (X))) 25:60
Q19597
error
error
3563
3563
DA:give_opinion shape:(X (X (X) (X)))

error
error
3563
3563
DA:give_opinion shape:(X (X (X (X))) 56:60
Q249648
3563
3563
DA:give_opinion shape:(X (X (X (X))) 57:60
Q19585
error
error
3563
3563
DA:give_opinion shape:(X (X (X (X))) 58:60
Q309059
error
error
3563
3563
DA:give_opinion shape:(X (X (X (X))) 59:60
Q6781508
error
error
3563
3563
DA:inform shape:(X (X (X))) 0:60
Q18656
3563
3563
DA:inform shape:(X (X (X))) 1:60
Q8682
3563
3563
DA:inform shape:(X (X (X))) 2:60
Q1130849
3563
3563
DA:inform shape:(X (X (X))) 3:60
Q9616
3563
3563
DA:inform shape:(X (X (X))) 4:60
Q483020
3563
3563
DA:inform shape:(X (X (X))) 5:60
Q7156
3563
3563
DA:inform shape:(X (X (X))) 6:60
Q9617
3563
3563
DA:inform shape:(X (X (X))) 7:60
Q50602
3563
3563
DA:inform shape:(X (X (X))) 8:60
Q18741
3563
3563
DA:inform shape:(X (X (X))) 9:60
Q157376
3563
3563
DA:inform shape:(X (X (X))) 10:60
Q15789
3563
3563
DA:inform shape:(X (X (X))) 11:60
Q18529
3563
3563
DA:inform shape:(X (X (X))) 12:60
Q1422
3563
3563
DA:inform shape:(X (X (X))) 13:60
Q19490
3563


3563
3563
DA:inform shape:(X (X) (X) (X (X))) 26:60
Q19481
3563
3563
DA:inform shape:(X (X) (X) (X (X))) 27:60
Q18747
3563
3563
DA:inform shape:(X (X) (X) (X (X))) 28:60
Q482764
3563
3563
DA:inform shape:(X (X) (X) (X (X))) 29:60
Q2641
3563
3563
DA:inform shape:(X (X) (X) (X (X))) 30:60
Q855809
3563
3563
DA:inform shape:(X (X) (X) (X (X))) 31:60
Q4791426
3563
3563
DA:inform shape:(X (X) (X) (X (X))) 32:60
Q1100222
3563
3563
DA:inform shape:(X (X) (X) (X (X))) 33:60
Q289613
3563
3563
DA:inform shape:(X (X) (X) (X (X))) 34:60
Q2037
3563
3563
DA:inform shape:(X (X) (X) (X (X))) 35:60
Q248782
3563
3563
DA:inform shape:(X (X) (X) (X (X))) 36:60
Q318348
3563
3563
DA:inform shape:(X (X) (X) (X (X))) 37:60
Q1324392
3563
3563
DA:inform shape:(X (X) (X) (X (X))) 38:60
Q837956
3563
3563
DA:inform shape:(X (X) (X) (X (X))) 39:60
Q1046367
3563
3563
DA:inform shape:(X (X) (X) (X (X))) 40:60
Q754307
3563
3563
DA:inform shape:(X (X) (X) (X (X))) 41:60
Q207462
3563
3563
DA:inform shape:(X (X) (X) (X (X

3563
3563
DA:inform shape:(X (X) (X) (X) (X (X))) 42:60
Q4874596
3563
3563
DA:inform shape:(X (X) (X) (X) (X (X))) 43:60
Q784965
3563
3563
DA:inform shape:(X (X) (X) (X) (X (X))) 44:60
Q738423
3563
3563
DA:inform shape:(X (X) (X) (X) (X (X))) 45:60
Q621120
3563
3563
DA:inform shape:(X (X) (X) (X) (X (X))) 46:60
Q212708
3563
3563
DA:inform shape:(X (X) (X) (X) (X (X))) 47:60
Q1243720
3563
3563
DA:inform shape:(X (X) (X) (X) (X (X))) 48:60
Q756594
3563
3563
DA:inform shape:(X (X) (X) (X) (X (X))) 49:60
Q1051514
3563
3563
DA:inform shape:(X (X) (X) (X) (X (X))) 50:60
Q622432
3563
3563
DA:inform shape:(X (X) (X) (X) (X (X))) 51:60
Q175687
3563
3563
DA:inform shape:(X (X) (X) (X) (X (X))) 52:60
Q5214935
3563
3563
DA:inform shape:(X (X) (X) (X) (X (X))) 53:60
Q219235
3563
3563
DA:inform shape:(X (X) (X) (X) (X (X))) 54:60
Q127635
3563
3563
DA:inform shape:(X (X) (X) (X) (X (X))) 55:60
Q1636019
3563
3563
DA:inform shape:(X (X) (X) (X) (X (X))) 56:60
Q249648
3563
3563
DA:inform shape:(X (X) (X

...

3556
3556
DA:recommend shape:(X (X (X))) 36:60
Q318348
3556
3556
DA:recommend shape:(X (X (X))) 37:60
Q1324392
3556
3556
DA:recommend shape:(X (X (X))) 38:60
Q837956
3556
3556
DA:recommend shape:(X (X (X))) 39:60
Q1046367
3556
3556
DA:recommend shape:(X (X (X))) 40:60
Q754307
3556
3556
DA:recommend shape:(X (X (X))) 41:60
Q207462
3556
3556
DA:recommend shape:(X (X (X))) 42:60
Q4874596
3556
3556
DA:recommend shape:(X (X (X))) 43:60
Q784965
3556
3556
DA:recommend shape:(X (X (X))) 44:60
Q738423
3556
3556
DA:recommend shape:(X (X (X))) 45:60
Q621120
3556
3556
DA:recommend shape:(X (X (X))) 46:60
Q212708
3556
3556
DA:recommend shape:(X (X (X))) 47:60
Q1243720
3556
3556
DA:recommend shape:(X (X (X))) 48:60
Q756594
3556
3556
DA:recommend shape:(X (X (X))) 49:60
Q1051514
3556
3556
DA:recommend shape:(X (X (X))) 50:60
Q622432
3556
3556
DA:recommend shape:(X (X (X))) 51:60
Q175687
3556
3556
DA:recommend shape:(X (X (X))) 52:60
Q5214935
3556
3556
DA:recommend shape:(X (X (X))) 53:60
Q219235
3556

3517
3517
DA:recommend shape:(X (X (X) (X))) 59:60
Q6781508
3517
3517
DA:recommend shape:(X (X (X (X))) 0:60
Q18656
3517
3517
DA:recommend shape:(X (X (X (X))) 1:60
Q8682
3517
3517
DA:recommend shape:(X (X (X (X))) 2:60
Q1130849
3517
3517
DA:recommend shape:(X (X (X (X))) 3:60
Q9616
3517
3517
DA:recommend shape:(X (X (X (X))) 4:60
Q483020
3517
3517
DA:recommend shape:(X (X (X (X))) 5:60
Q7156
3517
3517
DA:recommend shape:(X (X (X (X))) 6:60
Q9617
3517
3517
DA:recommend shape:(X (X (X (X))) 7:60
Q50602
3517
3517
DA:recommend shape:(X (X (X (X))) 8:60
Q18741
3517
3517
DA:recommend shape:(X (X (X (X))) 9:60
Q157376
3517
3517
DA:recommend shape:(X (X (X (X))) 10:60
Q15789
3517
3517
DA:recommend shape:(X (X (X (X))) 11:60
Q18529
3517
3517
DA:recommend shape:(X (X (X (X))) 12:60
Q1422
3517
3517
DA:recommend shape:(X (X (X (X))) 13:60
Q19490
3517
3517
DA:recommend shape:(X (X (X (X))) 14:60
Q1543
3517
3517
DA:recommend shape:(X (X (X (X))) 15:60
Q18716
3517
3517
DA:recommend shape:(X (X (X (X

3517
3517
DA:suggest shape:(X (X (X))) 18:60
Q631
3517
3517
DA:suggest shape:(X (X (X))) 19:60
Q81888
3517
3517
DA:suggest shape:(X (X (X))) 20:60
Q131371
3517
3517
DA:suggest shape:(X (X (X))) 21:60
Q41420
3517
3517
DA:suggest shape:(X (X (X))) 22:60
Q5794
3517
3517
DA:suggest shape:(X (X (X))) 23:60
Q18711
3517
3517
DA:suggest shape:(X (X (X))) 24:60
Q1128631
3517
3517
DA:suggest shape:(X (X (X))) 25:60
Q19597
3517
3517
DA:suggest shape:(X (X (X))) 26:60
Q19481
3517
3517
DA:suggest shape:(X (X (X))) 27:60
Q18747
3517
3517
DA:suggest shape:(X (X (X))) 28:60
Q482764
3517
3517
DA:suggest shape:(X (X (X))) 29:60
Q2641
3517
3517
DA:suggest shape:(X (X (X))) 30:60
Q855809
3517
3517
DA:suggest shape:(X (X (X))) 31:60
Q4791426
3517
3517
DA:suggest shape:(X (X (X))) 32:60
Q1100222
3517
3517
DA:suggest shape:(X (X (X))) 33:60
Q289613
3517
3517
DA:suggest shape:(X (X (X))) 34:60
Q2037
3517
3517
DA:suggest shape:(X (X (X))) 35:60
Q248782
3517
3517
DA:suggest shape:(X (X (X))) 36:60
Q318348
3517


3517
3517
DA:verify_attribute shape:(X (X) (X (X))) 36:60
Q318348
3517
3517
DA:verify_attribute shape:(X (X) (X (X))) 37:60
Q1324392
3517
3517
DA:verify_attribute shape:(X (X) (X (X))) 38:60
Q837956
3517
3517
DA:verify_attribute shape:(X (X) (X (X))) 39:60
Q1046367
3517
3517
DA:verify_attribute shape:(X (X) (X (X))) 40:60
Q754307
3517
3517
DA:verify_attribute shape:(X (X) (X (X))) 41:60
Q207462
3517
3517
DA:verify_attribute shape:(X (X) (X (X))) 42:60
Q4874596
3517
3517
DA:verify_attribute shape:(X (X) (X (X))) 43:60
Q784965
3517
3517
DA:verify_attribute shape:(X (X) (X (X))) 44:60
Q738423
3517
3517
DA:verify_attribute shape:(X (X) (X (X))) 45:60
Q621120
3517
3517
DA:verify_attribute shape:(X (X) (X (X))) 46:60
Q212708
3517
3517
DA:verify_attribute shape:(X (X) (X (X))) 47:60
Q1243720
3517
3517
DA:verify_attribute shape:(X (X) (X (X))) 48:60
Q756594
3517
3517
DA:verify_attribute shape:(X (X) (X (X))) 49:60
Q1051514
3517
3517
DA:verify_attribute shape:(X (X) (X (X))) 50:60
Q622432
3517


3517
3517
DA:verify_attribute shape:(X (X (X (X))) 42:60
Q4874596
3517
3517
DA:verify_attribute shape:(X (X (X (X))) 43:60
Q784965
3517
3517
DA:verify_attribute shape:(X (X (X (X))) 44:60
Q738423
3517
3517
DA:verify_attribute shape:(X (X (X (X))) 45:60
Q621120
3517
3517
DA:verify_attribute shape:(X (X (X (X))) 46:60
Q212708
3517
3517
DA:verify_attribute shape:(X (X (X (X))) 47:60
Q1243720
3517
3517
DA:verify_attribute shape:(X (X (X (X))) 48:60
Q756594
3517
3517
DA:verify_attribute shape:(X (X (X (X))) 49:60
Q1051514
3517
3517
DA:verify_attribute shape:(X (X (X (X))) 50:60
Q622432
3517
3517
DA:verify_attribute shape:(X (X (X (X))) 51:60
Q175687
3517
3517
DA:verify_attribute shape:(X (X (X (X))) 52:60
Q5214935
3517
3517
DA:verify_attribute shape:(X (X (X (X))) 53:60
Q219235
3517
3517
DA:verify_attribute shape:(X (X (X (X))) 54:60
Q127635
3517
3517
DA:verify_attribute shape:(X (X (X (X))) 55:60
Q1636019
3517
3517
DA:verify_attribute shape:(X (X (X (X))) 56:60
Q249648
3517
3517
DA:verify_